## 第四次讀書會-第3組

### 針對ptt數位中介服務法爭議事件，進行社會網路分析

- 課程：社群媒體分析
- 授課教授：黃三益
- 組長：B084020041劉怡謙
- 組員：B094020042黃萱妮、B084020009程尤欣、M114020052王渙鈞、姚昀誠、劉杰煊、B065040041蔡瑋駿、M114020055吳均庭

## Outline
- 引入套件
1. About data
    - 1.1 分析動機及目的
    - 1.2 資料集基本檢視
2. 衡量節點間的關係
    - 2.1 畫出文章、發文者、評論者的網路
    - 2.2 計算網友之間的關係
3. 衡量社群網路 - Transitivity/Density/Distance/Diameter/Clustering

#### 引入需要的套件

In [1]:
import pandas as pd
import numpy as np
import pyvis
import networkx as nx
import IPython

## About data
### 分析動機及目的
用Graph繪製的方式，試圖找出發文者及回文者之間之關係。
#### 引入資料

In [19]:
raw_data = pd.read_csv('./data.csv', encoding = "utf_8_sig")
raw_data = raw_data[raw_data.artComment != '[]']
raw_data = raw_data.sample(round(raw_data.shape[0]/64))
print(raw_data.shape)
raw_data.head()

(27, 11)


system_id                                             artUrl   
513         514  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  \
1344       1345  https://www.ptt.cc/bbs/Gossiping/M.1661560990....   
812         813  https://www.ptt.cc/bbs/Gossiping/M.1660974925....   
901         902  https://www.ptt.cc/bbs/Gossiping/M.1661009323....   
1116       1117  https://www.ptt.cc/bbs/Gossiping/M.1661165890....   

                         artTitle              artDate     artPoster   
513              [問卦]中國是塔綠班的理想國度?  2022-08-19 14:39:22  StarTouching  \
1344           [問卦]八月底了，那個台積高雄廠呢？  2022-08-27 08:43:08       ryo1008   
812      [問卦]ptt創始人杜奕瑾針對數位中介法發表意見  2022-08-20 13:55:23      nk11208z   
901   Re:[新聞]Bump認父親黑道背景喊冤「沒有使用違法  2022-08-20 23:28:41  ptt987654321   
1116           [問卦]兩警的殉職難道又救了民進黨？  2022-08-22 18:58:08    Zoetermeer   

     artCatagory                                         artContent   
513    Gossiping  最近看到吱吱覺青說說\n\n有了數位中介法\n\n就可以不被錯誤訊息洗腦\n\n還可以保護小...  \
1344   Gossiping  在歷經各種被動工之後八月終於快過了\n依照18廠那種複製貼上般的蓋廠速度\n高雄廠應該也蓋得...   
812    Gossiping  先上FB文章 以下是全文\n\n認知操作產業、數位平台收益與言論自由\n台灣是亞洲同時為新聞...   
901    Gossiping  剛剛無聊想看看棒有沒有上發燒\n想當然沒有\n因為過多檢舉當然不會上\n\n這就是中介法要的...   
1116   Gossiping  我說\n台灣缺電後的能源問題呢\n中共軍演後的國防問題呢\n經貿制裁後的經濟問題呢\n論文門...   

                                             artComment             e_ip   
513   [{"cmtStatus": "推", "cmtPoster": "lienjj", "cm...    211.72.117.63  \
1344  [{"cmtStatus": "→", "cmtPoster": "ulli", "cmtC...              NaN   
812   [{"cmtStatus": "→", "cmtPoster": "johnwu", "cm...       1.34.16.89   
901   [{"cmtStatus": "推", "cmtPoster": "VOLK11", "cm...     111.241.9.20   
1116  [{"cmtStatus": "噓", "cmtPoster": "HDSM", "cmtC...  118.231.216.222   

             insertedDate dataSource  
513   2022-08-20 01:38:57        ptt  
1344  2022-08-28 01:31:02        ptt  
812   2022-08-21 01:37:54        ptt  
901   2022-08-21 01:43:28        ptt  
1116  2022-08-23 01:37:06        ptt

In [20]:
#parse comment

def getComtInfo(com):
  cmters,cmt_statuss = [],[]
  com = eval(com)
  for i in com:
    print(i)
    cmters.append(i['cmtPoster'])
    cmt_statuss.append(i['cmtStatus'])
  return pd.Series([cmters, cmt_statuss])

raw_data[['artComter','artStatus']] = raw_data['artComment'].apply(lambda r: getComtInfo(r))

{'cmtStatus': '推', 'cmtPoster': 'lienjj', 'cmtContent': ':是的', 'cmtDate': '2022-08-19 14:39:00'}
{'cmtStatus': '→', 'cmtPoster': 'lienjj', 'cmtContent': ':跟台灣吊路燈比送勞改好像好一點', 'cmtDate': '2022-08-19 14:40:00'}
{'cmtStatus': '→', 'cmtPoster': 'kent', 'cmtContent': ':中國台灣也是中國的一部份', 'cmtDate': '2022-08-19 14:40:00'}
{'cmtStatus': '噓', 'cmtPoster': 'Iceascool', 'cmtContent': ':塔綠班竟然通匪了', 'cmtDate': '2022-08-19 14:40:00'}
{'cmtStatus': '推', 'cmtPoster': 'ilovemiao', 'cmtContent': ':是', 'cmtDate': '2022-08-19 14:40:00'}
{'cmtStatus': '推', 'cmtPoster': 'Howard61313', 'cmtContent': ':為了抗中保台建議小粉綠全部送中', 'cmtDate': '2022-08-19 14:40:00'}
{'cmtStatus': '→', 'cmtPoster': 'cck525', 'cmtContent': ':都是韭菜還拼命幫掌權者講話有夠智障', 'cmtDate': '2022-08-19 14:40:00'}
{'cmtStatus': '→', 'cmtPoster': 'banbanzon', 'cmtContent': ':智登早就想搞了', 'cmtDate': '2022-08-19 14:41:00'}
{'cmtStatus': '→', 'cmtPoster': 'minhua2012', 'cmtContent': ':開始懷疑塔綠班是不是老共派來臥底的', 'cmtDate': '2022-08-19 14:41:00'}
{'cmtStatus': '推', 'cmtPoster': 'JM

In [21]:
raw_data = raw_data.explode(['artComter','artStatus'])
social_data = raw_data[['artUrl','artPoster','artComter','artStatus']]
social_data.head(10)

artUrl     artPoster   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching  \
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   

       artComter artStatus  
513       lienjj         推  
513       lienjj         →  
513         kent         →  
513    Iceascool         噓  
513    ilovemiao         推  
513  Howard61313         推  
513       cck525         →  
513    banbanzon         →  
513   minhua2012         →  
513     JMichael         推

In [22]:
social_data.artStatus.unique()


array(['推', '→', '噓'], dtype=object)

## 2. 衡量節點間的關係

### 2.1 畫出文章、發文者、評論者的網路

In [23]:
# 建立邊的資料
import random


po_df = social_data[['artPoster','artUrl']].drop_duplicates().rename(columns = {'artPoster':'src','artUrl':'dis'})
sample_url = random.choices(po_df.dis.unique().tolist(),k=300)
po_df = po_df[po_df.dis.isin(sample_url)]
re_df = social_data[['artComter','artUrl','artStatus']].rename(columns = {'artComter':'src','artUrl':'dis','artStatus':'weight'})
re_df = re_df[re_df.dis.isin(sample_url)]
re_df = re_df[~re_df['src'].isna()]



def convertStatus(s):
  if s == '推':
    return 2
  elif s == '→':
    return 1
  else :
    return -1
re_df['weight'] = re_df['weight'].map(convertStatus)
re_df = re_df.groupby(['src','dis']).sum().reset_index()

# 設定分數低的為紅色
def getColor(w):
  if w>0:
    return 'green'
  else:
    return 'red'
re_df['color'] = re_df.weight.map(getColor)

In [24]:
re_df

src                                                dis  weight   
0        A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1660897357....       1  \
1        A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1660974925....      -1   
2        A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1661214388....       1   
3         APUDOOR  https://www.ptt.cc/bbs/Gossiping/M.1662334712....      -1   
4         ARTORIA  https://www.ptt.cc/bbs/Gossiping/M.1661214388....       2   
...           ...                                                ...     ...   
1415       zukigo  https://www.ptt.cc/bbs/Gossiping/M.1660974925....       4   
1416     zxc90147  https://www.ptt.cc/bbs/Gossiping/M.1660838393....       2   
1417  zxcelephant  https://www.ptt.cc/bbs/Gossiping/M.1660974925....      -1   
1418         zzro  https://www.ptt.cc/bbs/Gossiping/M.1660838393....      -1   
1419     zzzzaaaa  https://www.ptt.cc/bbs/Gossiping/M.1661680393....       1   

      color  
0     green  
1       red  
2     green  
3       red  
4     green  
...     ...  
1415  green  
1416  green  
1417    red  
1418    red  
1419  green  

[1420 rows x 4 columns]

In [25]:
# 人為綠色節點
# po文為橘色節點

netWork = pyvis.network.Network(notebook=True, cdn_resources='in_line',directed=True)
#netWork = netWork.replace('\xa9', ' ') 
person = list(set(po_df.src.unique().tolist()+re_df.src.unique().tolist()))
url = po_df.dis.unique().tolist()
netWork.add_nodes(
    nodes = person,
    value = [1 for i in range(len(person))],
    color = ['#66CDAA' for i in range(len(person))],
    title = person
)
netWork.add_nodes(
    nodes = url,
    value = [2 for i in range(len(url))],
    color = ['#FFB366' for i in range(len(url))],
    title = url
)
for i in po_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color='grey')
for i in re_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color=i[3])

# 設定layout
netWork.repulsion()


# netWork.toggle_physics(True)
# netWork.set_options("""
# const options = {
#   "physics": {
#     "forceAtlas2Based": {
#       "springLength": 100
#     },
#     "minVelocity": 0.75,
#     "solver": "forceAtlas2Based",
#     "timestep": 0.48
#   }
# }
# """)


netWork.show("./basic_netWork.html")
IPython.display.HTML('basic_netWork.html')

./basic_netWork.html


從圖中可以看出討論度最高的幾篇都是噓文佔了大多數

### 2.2 計算網友之間的關係

In [26]:
pos_cmt = social_data.copy()
pos_cmt = pos_cmt[~pos_cmt.artComter.isna()]
pos_cmt.head(10)

artUrl     artPoster   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching  \
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   
513  https://www.ptt.cc/bbs/Gossiping/M.1660891165....  StarTouching   

       artComter artStatus  
513       lienjj         推  
513       lienjj         →  
513         kent         →  
513    Iceascool         噓  
513    ilovemiao         推  
513  Howard61313         推  
513       cck525         →  
513    banbanzon         →  
513   minhua2012         →  
513     JMichael         推

In [27]:
pos_cmt['score'] = pos_cmt['artStatus'].apply(lambda r: convertStatus(r))
pos_cmt = pos_cmt.groupby(['artComter','artPoster']).sum('score').reset_index()
pos_cmt = pos_cmt[pos_cmt.score>=0]
pos_cmt = pos_cmt[pos_cmt.artComter != pos_cmt.artPoster]
# pos_cmt.score = 1
pos_cmt

artComter     artPoster  score
0       A80211ab  louiswei1986      1
2       A80211ab      sal60614      1
4        ARTORIA      sal60614      2
5          ASEVE      nk11208z      0
6        ASUSboy   destiny4886      1
...          ...           ...    ...
1412  zerowingtw      nk11208z      1
1413      zhen10     Workforme      1
1415      zukigo      nk11208z      4
1416    zxc90147   HollisterCo      2
1419    zzzzaaaa    JohnLackey      1

[955 rows x 3 columns]

In [28]:
pers = np.unique(pos_cmt[['artComter', 'artPoster']])
mat = pd.pivot_table(pos_cmt,index = 'artComter', columns = 'artPoster' ,values='score' ).fillna(0)\
  .reindex(columns=pers, index=pers, fill_value=0).to_numpy()
print(mat.shape)
tri = (np.tril(mat,-1).T + np.triu(mat,1))
mat_s = tri+tri.T

(882, 882)


In [29]:
def random_color():
  r = lambda: random.randint(0,255)
  return '#%02X%02X%02X' % (r(),r(),r())

def matPresentGraph(mat:np.array,node_id:list,node_type:list=None,node_value:list = None,directed = True,edge_color=None) -> pyvis.network.Network:

  if directed != True:
    if (mat == mat.transpose()).all():
      print('matrix is Symmetric')
    else:
      print('matrix is not Symmetric')
  if node_type == None:
    c = random_color()
    node_colors = [c for i in range(len(node_id))]
    node_type = [" " for i in range(len(node_id))]
  else:
    node_color_map = {}
    for i in set(node_type):
      while True:
        c = random_color()
        if c not in node_color_map.values():
          break
      node_color_map[i] = c
    node_colors = [node_color_map[i] for i in node_type]
  # print(node_colors)
  if edge_color == None:
    edge_color = random_color()
  edge_color = random_color()
  if node_value == None:
    node_value = [1 for i in range(len(node_id))]

  net = pyvis.network.Network(notebook=True, directed = directed, cdn_resources='in_line')
  
  titles_list = []
  for i ,j in zip(node_id,node_type):
    titles_list.append(str(i)+":"+str(j))

  net.add_nodes(
      nodes = node_id,
      value = node_value,
      label = node_id,
      title = titles_list,
      color = node_colors
  )

  for row in range(len(node_id)):
    for col in range(len(node_id)):
      if mat[row][col]>0.:
        net.add_edge(
            node_id[row],node_id[col],width = mat[row][col],color = edge_color,title = mat[row][col]
        )
  net.repulsion()
  return net


In [30]:
# 定義發文者（po）、評論者(cmt)、兩者兼具(both)
node_type = []

cmt_list = pos_cmt['artComter'].unique().tolist()
po_list = pos_cmt['artPoster'].unique().tolist()
both_list = list(set(cmt_list) & set(po_list))
for p in pers:
  if p in both_list:
    node_type.append('both')

  elif p in cmt_list:
    node_type.append('cmt')

  elif p in po_list:
    node_type.append('po')

In [31]:
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type)
net.show("./pers_netWork.html")
IPython.display.HTML('pers_netWork.html')

./pers_netWork.html


大部分的網友只回了一篇文章，少數回了兩篇以上的文章。而數量上也可以看出，有蠻多網友非常熱衷於討論單一文章（線條較寬）。

### 2.3 計算 eigen vector

In [32]:
eigenvec = np.array(list(nx.eigenvector_centrality(nx.Graph(mat_s),max_iter = 10000).values()))
eigenvec = (eigenvec-np.min(eigenvec))/(np.max(eigenvec)-np.min(eigenvec))

In [33]:
q = np.quantile(eigenvec,[.2,.4,.6,.8])
q

array([0.00085154, 0.00177443, 0.0133164 , 0.04668026])

In [34]:
node_value = []


for i in eigenvec:

  if i > q[3]:
    node_value.append(25)
  elif i >q[2]:
    node_value.append(20)
  elif i>q[1]:
    node_value.append(15)
  elif i>q[0]:
    node_value.append(10)
  else:
    node_value.append(5)
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value = node_value,directed=False)
net.show("./pers_eig_netWork.html")
IPython.display.HTML('pers_eig_netWork.html')

matrix is not Symmetric
./pers_eig_netWork.html


eigen vector 主要意義為連結到越多重要的人代表越重要。所以從圖中可以看出，發文者因為跟許多人有連結，故越熱門的文章會視為越重要（node越大）。而對回文者來說，若他回了比較熱門的文章，或是回了一個以上的文章，也會被視為重要性較高

### 2.4 normalize 的 eigen vector - PageRank

In [35]:
# Digraph 設定有向圖
pagerank = np.array(list(nx.pagerank(nx.DiGraph(mat)).values()))
# pagerank = (pagerank-np.min(pagerank))/(np.max(pagerank)-np.min(pagerank))
pagerank

array([0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.02026487, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.02499289, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00280122, 0.00063631, 0.00063631,
       0.00063631, 0.00063631, 0.00063631, 0.08346334, 0.00063

In [36]:
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=(pagerank*1000).tolist())
net.show("./pers_page_netWork.html")
IPython.display.HTML('pers_page_netWork.html')

./pers_page_netWork.html


用page rank來衡量後，可以發現真正較為重要的是那些in-degree特別多的，也就是較為熱門的文章

### 2.5 Hits score （有向圖）

In [37]:
out_,in_ = nx.hits(nx.DiGraph(mat),max_iter=100)
out_,in_ = np.array(list(out_.values())),np.array(list(in_.values()))
out_ = (out_-np.min(out_))/(np.max(out_)-np.min(out_))
in_ = (in_-np.min(in_))/(np.max(in_)-np.min(in_))

In [38]:
in_q = np.quantile(in_,[.2,.4,.6,.8])
out_q = np.quantile(out_,[.2,.4,.6,.8])

In [39]:
node_value = []


for i in out_:
  if i > out_q[3]:
    node_value.append(25)
  elif i >out_q[2]:
    node_value.append(20)
  elif i>out_q[1]:
    node_value.append(15)
  elif i>out_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_out_netWork.html")
IPython.display.HTML('pers_out_netWork.html')

./pers_out_netWork.html


用out-degree 來衡量hit score，可以發現跟前面的結果蠻類似的，可以看出那些node較大的帳號比較熱衷於討論，而比較有趣的現象是發文者幾乎都不會做回應

In [40]:
node_value = []
for i in in_:
  if i > in_q[3]:
    node_value.append(25)
  elif i >in_q[2]:
    node_value.append(20)
  elif i>in_q[1]:
    node_value.append(15)
  elif i>in_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_in_netWork.html")
IPython.display.HTML('pers_in_netWork.html')

./pers_in_netWork.html


### 2.6 betweenness centrality

In [41]:
bet = np.array(list(nx.betweenness_centrality(nx.Graph(mat_s)).values()))
bet = (bet-np.min(bet))/(np.max(bet)-np.min(bet))
bet_q = np.quantile(bet,[.2,.4,.6,.8])

In [42]:
node_value = []
for i in bet:
  if i > bet_q[3]:
    node_value.append(25)
  elif i > bet_q[2]:
    node_value.append(20)
  elif i>bet_q[1]:
    node_value.append(15)
  elif i>bet_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_bet_netWork.html")
IPython.display.HTML('pers_bet_netWork.html')

./pers_bet_netWork.html


從betweenness centrality可以看出那些在比較多篇文章都有回文的帳號

## 3. 衡量社群網路 - Transitivity/Density/Distance/Diameter/Clustering



計算最大的subgraph 的 measure

In [43]:
# 計算max subgraph
G = nx.Graph(mat_s)
G_sub = sorted(nx.connected_components(G), key=len, reverse=True)
G_max_sub = G.subgraph(G_sub[0])
# # 重新定義 mat
sub_mat = nx.adjacency_matrix(G_max_sub).todense()
node_idx = list(G_max_sub.nodes)
sub_pers = pers[node_idx]

In [44]:
net = matPresentGraph(mat=sub_mat,node_id=sub_pers,directed=False)
net.show("./max_sub.html")
IPython.display.HTML('max_sub.html')

matrix is Symmetric
./max_sub.html


計算transitivity


In [45]:
nx.transitivity(nx.Graph(sub_mat))

0

計算density 及 distance
從density中可以看出，edge並沒有很密集，因此distance蠻長的

In [46]:
nx.density(nx.Graph(sub_mat))

0.0026650186159388614

In [47]:
nx.average_shortest_path_length(nx.Graph(sub_mat))

4.385610708310095

計算diameter 

In [48]:
nx.diameter(nx.Graph(sub_mat))

10

計算clustering

In [49]:
nx.average_clustering(nx.Graph(sub_mat))

0.0